In [1]:
!nvidia-smi

Fri Dec  6 10:05:23 2024       
+-----------------------------------------------------------------------------------------+
| NVIDIA-SMI 566.36                 Driver Version: 566.36         CUDA Version: 12.7     |
|-----------------------------------------+------------------------+----------------------+
| GPU  Name                  Driver-Model | Bus-Id          Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |           Memory-Usage | GPU-Util  Compute M. |
|                                         |                        |               MIG M. |
|=========================================+========================+======================|
|   0  NVIDIA GeForce RTX 3050 ...  WDDM  |   00000000:01:00.0 Off |                  N/A |
| N/A   43C    P8              6W /   75W |     204MiB /   4096MiB |      0%      Default |
|                                         |                        |                  N/A |
+-----------------------------------------+-----

In [2]:
import os
HOME = os.getcwd()
print(HOME)

C:\Users\ganji\Codes\Mini Proj


In [3]:
!pip install ultralytics==8.0.20

from IPython import display
display.clear_output()

import ultralytics
ultralytics.checks()

Ultralytics YOLOv8.0.20  Python-3.9.20 torch-2.5.1 CUDA:0 (NVIDIA GeForce RTX 3050 Laptop GPU, 4096MiB)
Setup complete  (12 CPUs, 7.6 GB RAM, 328.2/475.8 GB disk)


In [4]:
from ultralytics import YOLO

from IPython.display import display, Image

In [5]:
%cd {HOME}
!yolo task=detect mode=predict model=yolov8n.pt conf=0.25 source='https://media.roboflow.com/notebooks/examples/dog.jpeg'

C:\Users\ganji\Codes\Mini Proj


C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\IPython\core\magics\osm.py:417: UserWarning: using dhist requires you to install the `pickleshare` library.
  self.shell.db['dhist'] = compress_dhist(dhist)[-100:]
'yolo' is not recognized as an internal or external command,
operable program or batch file.


In [6]:
model = YOLO(f'{HOME}/yolov8n.pt')
results = model.predict(source='https://media.roboflow.com/notebooks/examples/dog.jpeg', conf=0.25)

C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\ultralytics\nn\tasks.py:332: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return torch.load(file, map_location='cpu') 

In [7]:
results[0].boxes.xyxy

tensor([[   0.,  315.,  625., 1278.],
        [  55.,  250.,  648., 1266.],
        [ 633.,  720.,  701.,  786.]], device='cuda:0')

In [8]:
results[0].boxes.conf

tensor([0.72685, 0.29132, 0.28402], device='cuda:0')

In [9]:
results[0].boxes.cls

tensor([ 0., 16.,  2.], device='cuda:0')

In [10]:
from ultralytics import YOLO

# Change to your dataset directory
%cd C:/Users/ganji/Downloads/Weapon 2.v2i.yolov8

# Load the YOLOv8 model
model = YOLO('yolov8s.pt')

# Train the model
results = model.train(data='data.yaml', epochs=40, imgsz=224, batch=8, plots=True)



C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\IPython\core\magics\osm.py:417: UserWarning: using dhist requires you to install the `pickleshare` library.
  self.shell.db['dhist'] = compress_dhist(dhist)[-100:]
C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\ultralytics\nn\tasks.py:332: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `we

C:\Users\ganji\Downloads\Weapon 2.v2i.yolov8


  7                  -1  1   1180672  ultralytics.nn.modules.Conv                  [256, 512, 3, 2]              
  8                  -1  1   1838080  ultralytics.nn.modules.C2f                   [512, 512, 1, True]           
  9                  -1  1    656896  ultralytics.nn.modules.SPPF                  [512, 512, 5]                 
 10                  -1  1         0  torch.nn.modules.upsampling.Upsample         [None, 2, 'nearest']          
 11             [-1, 6]  1         0  ultralytics.nn.modules.Concat                [1]                           
 12                  -1  1    591360  ultralytics.nn.modules.C2f                   [768, 256, 1]                 
 13                  -1  1         0  torch.nn.modules.upsampling.Upsample         [None, 2, 'nearest']          
 14             [-1, 4]  1         0  ultralytics.nn.modules.Concat                [1]                           
 15                  -1  1    148224  ultralytics.nn.modules.C2f                   [384,

In [20]:
# Single Camera Detection #
import torch
import torchreid
import cv2
import torchvision.transforms as transforms
from ultralytics import YOLO
import numpy as np
from sklearn.metrics.pairwise import cosine_similarity
from collections import deque

# Load YOLO models for weapon and person detection
weapon_model = YOLO(r'C:\Users\ganji\Downloads\Weapon 2.v2i.yolov8\runs\detect\train4\weights\best.pt')
person_model = YOLO(r'C:\Users\ganji\Downloads\People Detection.v8i.yolov8\runs\detect\train\weights\best.pt')

# Initialize OSNet re-ID model
reid_model = torchreid.models.build_model('osnet_x1_0', num_classes=1000, pretrained=True)
reid_model.eval()
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
reid_model = reid_model.to(device)

# Transform for re-ID
transform = transforms.Compose([
    transforms.ToPILImage(),
    transforms.Resize((256, 128)),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
])

# Store embeddings and assigned IDs
person_database = {}
person_history = {}  # Keep history of features for each person
current_id = 1  # Start ID count
max_history_size = 5  # Number of frames to track the history of embeddings

def normalize_embedding(features):
    return features / np.linalg.norm(features)  # Normalize the embeddings

def get_person_id(features, threshold=0.6):
    global current_id
    
    # Normalize the features before comparing
    features = normalize_embedding(features)
    
    # Compare features to those in the database
    for person_id, data in person_database.items():
        existing_features = normalize_embedding(data['features'])
        similarity = cosine_similarity(features.reshape(1, -1), existing_features.reshape(1, -1))
        
        print(f"Comparing features, Similarity: {similarity[0][0]} for Person ID: {person_id}")  # Debugging similarity
        
        if similarity[0][0] >= threshold:
            # Update history
            if person_id in person_history:
                person_history[person_id].append(features)
                if len(person_history[person_id]) > max_history_size:
                    person_history[person_id].pop(0)  # Keep track of the latest embeddings
            else:
                person_history[person_id] = deque([features], maxlen=max_history_size)
            return person_id  # Return existing ID if similarity is above threshold

    # Assign new ID if no match found
    person_database[current_id] = {'features': features}
    person_history[current_id] = deque([features], maxlen=max_history_size)
    assigned_id = current_id
    current_id += 1
    print(f"New person detected, Assigned ID: {assigned_id}")  # Debugging new ID
    return assigned_id

# Open video capture
cap = cv2.VideoCapture(0)

while cap.isOpened():
    ret, frame = cap.read()
    if not ret:
        break

    # Weapon detection
    weapon_results = weapon_model(frame)
    weapon_boxes = weapon_results[0].boxes.xyxy
    weapon_classes = weapon_results[0].boxes.cls

    # Person detection
    person_results = person_model(frame)
    person_boxes = person_results[0].boxes.xyxy

    for i, weapon_box in enumerate(weapon_boxes):
        weapon_class_id = int(weapon_classes[i])

        if weapon_class_id in [0, 1]:  # Assuming 0 and 1 are the weapon class IDs
            wx1, wy1, wx2, wy2 = map(int, weapon_box)

            # Process persons near weapon
            for person_box in person_boxes:
                px1, py1, px2, py2 = map(int, person_box[:4])

                if (wx1 < px2 and wx2 > px1 and wy1 < py2 and wy2 > py1):
                    # Extract and transform person image for re-ID
                    person_img = frame[py1:py2, px1:px2]
                    person_img_tensor = transform(person_img).unsqueeze(0).to(device)

                    with torch.no_grad():
                        person_features = reid_model(person_img_tensor).cpu().numpy().flatten()

                    # Get unique stable ID for the person
                    person_id = get_person_id(person_features)

                    # Draw bounding boxes and ID labels
                    cv2.rectangle(frame, (px1, py1), (px2, py2), (255, 0, 0), 2)
                    cv2.putText(frame, f'Person ID: {person_id}', (px1, py1 - 10),
                                cv2.FONT_HERSHEY_SIMPLEX, 0.5, (255, 0, 0), 2)
                    cv2.rectangle(frame, (wx1, wy1), (wx2, wy2), (0, 255, 0), 2)
                    cv2.putText(frame, "Weapon", (wx1, wy1 - 10),
                                cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0, 255, 0), 2)

    # Display the frame
    cv2.imshow('Weapon Detection & Re-ID', frame)

    if cv2.waitKey(1) & 0xFF == ord('q'):
        break

cap.release()
cv2.destroyAllWindows()

C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\ultralytics\nn\tasks.py:332: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return torch.load(file, map_location='cpu') 

Successfully loaded imagenet pretrained weights from "C:\Users\ganji/.cache\torch\checkpoints\osnet_x1_0_imagenet.pth"


Ultralytics YOLOv8.0.20  Python-3.9.20 torch-2.5.1 CUDA:0 (NVIDIA GeForce RTX 3050 Laptop GPU, 4096MiB)
Model summary (fused): 168 layers, 11126358 parameters, 0 gradients, 28.4 GFLOPs
Ultralytics YOLOv8.0.20  Python-3.9.20 torch-2.5.1 CUDA:0 (NVIDIA GeForce RTX 3050 Laptop GPU, 4096MiB)
Model summary (fused): 168 layers, 11125971 parameters, 0 gradients, 28.4 GFLOPs


New person detected, Assigned ID: 1
Comparing features, Similarity: 0.9485009908676147 for Person ID: 1
Comparing features, Similarity: 0.9472410678863525 for Person ID: 1
Comparing features, Similarity: 0.8351741433143616 for Person ID: 1
Comparing features, Similarity: 0.9367756247520447 for Person ID: 1
Comparing features, Similarity: 0.539607048034668 for Person ID: 1
New person detected, Assigned ID: 2
Comparing features, Similarity: 0.9421694874763489 for Person ID: 1
Comparing features, Similarity: 0.8407605886459351 for Person ID: 1
Comparing features, Similarity: 0.9639698266983032 for Person ID: 1
Comparing features, Similarity: 0.8553578853607178 for Person ID: 1
Comparing features, Similarity: 0.9245482087135315 for Person ID: 1
Comparing features, Similarity: 0.6495464444160461 for Person ID: 1
Comparing features, Similarity: 0.7668787240982056 for Person ID: 1
Comparing features, Similarity: 0.5714571475982666 for Person ID: 1
Comparing features, Similarity: 0.89726340770

In [ ]:
# Single Camera with Pop-up Notification #
import torch
import torchreid
import cv2
import torchvision.transforms as transforms
from ultralytics import YOLO
import numpy as np
from sklearn.metrics.pairwise import cosine_similarity
import tkinter as tk
from PIL import Image, ImageTk
import threading

# Load YOLO models for weapon and person detection
weapon_model = YOLO(r'C:\Users\ganji\Downloads\Weapon 2.v2i.yolov8\runs\detect\train4\weights\best.pt')
person_model = YOLO(r'C:\Users\ganji\Downloads\People Detection.v8i.yolov8\runs\detect\train\weights\best.pt')

# Initialize OSNet re-ID model
reid_model = torchreid.models.build_model('osnet_x1_0', num_classes=1000, pretrained=True)
reid_model.eval()
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
reid_model = reid_model.to(device)

# Transform for re-ID
transform = transforms.Compose([
    transforms.ToPILImage(),
    transforms.Resize((256, 128)),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
])

# Store embeddings and assigned IDs
person_database = {}
flagged_person_id = None  # ID of the person detected with a weapon

# Popup function for alert
def show_popup(person_image):
    popup = tk.Tk()
    popup.title("Warning: Possible Threat Detected")
    popup.geometry("300x400")
    tk.Label(popup, text="Threat Detected!", font=("Helvetica", 16), fg="red").pack(pady=10)

    if person_image is not None:
        person_img_pil = Image.fromarray(person_image)
        person_img_pil.thumbnail((250, 250))
        img_tk = ImageTk.PhotoImage(person_img_pil)
        img_label = tk.Label(popup, image=img_tk)
        img_label.image = img_tk
        img_label.pack(pady=10)

    tk.Button(popup, text="OK", command=popup.destroy).pack(pady=10)
    popup.mainloop()

# Trigger the popup notification in a new thread
def trigger_popup(person_image):
    threading.Thread(target=show_popup, args=(person_image,)).start()

# Normalizing embeddings
def normalize_embedding(features):
    return features / np.linalg.norm(features)

# Get a unique ID or reuse ID for the person based on similarity threshold
def get_person_id(features, threshold=0.7):
    global flagged_person_id
    features = normalize_embedding(features)

    for person_id, existing_data in person_database.items():
        existing_features = normalize_embedding(existing_data['features'])
        similarity = cosine_similarity(features.reshape(1, -1), existing_features.reshape(1, -1))
        
        if similarity >= threshold:
            return person_id  # Return existing ID if a match is found

    new_id = len(person_database) + 1
    person_database[new_id] = {'features': features}
    return new_id

cap = cv2.VideoCapture(0)

while cap.isOpened():
    ret, frame = cap.read()
    if not ret:
        break

    # Weapon detection
    weapon_results = weapon_model(frame)
    weapon_boxes = weapon_results[0].boxes.xyxy
    weapon_classes = weapon_results[0].boxes.cls

    # Person detection
    person_results = person_model(frame)
    person_boxes = person_results[0].boxes.xyxy

    weapon_detected = False
    person_image_with_weapon = None

    for i, weapon_box in enumerate(weapon_boxes):
        weapon_class_id = int(weapon_classes[i])

        if weapon_class_id in [0, 1]:  # Assuming weapon class IDs are 0 and 1
            wx1, wy1, wx2, wy2 = map(int, weapon_box)
            weapon_detected = True

            # Process persons near the weapon
            for person_box in person_boxes:
                px1, py1, px2, py2 = map(int, person_box[:4])

                if (wx1 < px2 and wx2 > px1 and wy1 < py2 and wy2 > py1):
                    person_img = frame[py1:py2, px1:px2]
                    person_img_tensor = transform(person_img).unsqueeze(0).to(device)

                    with torch.no_grad():
                        person_features = reid_model(person_img_tensor).cpu().numpy().flatten()

                    person_id = get_person_id(person_features)

                    # If the person has a weapon, flag them
                    flagged_person_id = person_id
                    person_image_with_weapon = person_img

                    # Draw bounding boxes and ID labels for flagged person
                    cv2.rectangle(frame, (px1, py1), (px2, py2), (255, 0, 0), 2)
                    cv2.putText(frame, f'Flagged ID: {person_id} (Weapon)', (px1, py1 - 10),
                                cv2.FONT_HERSHEY_SIMPLEX, 0.5, (255, 0, 0), 2)
                    cv2.rectangle(frame, (wx1, wy1), (wx2, wy2), (0, 255, 0), 2)
                    cv2.putText(frame, "Weapon", (wx1, wy1 - 10),
                                cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0, 255, 0), 2)

                    # Trigger the popup notification with the person's image
                    trigger_popup(person_image_with_weapon)

    # Process each person detected in the frame, regardless of weapon detection
    for person_box in person_boxes:
        px1, py1, px2, py2 = map(int, person_box[:4])
        person_img = frame[py1:py2, px1:px2]
        person_img_tensor = transform(person_img).unsqueeze(0).to(device)

        with torch.no_grad():
            person_features = reid_model(person_img_tensor).cpu().numpy().flatten()

        person_id = get_person_id(person_features)

        # Draw bounding box only for the flagged person, even without a weapon
        if person_id == flagged_person_id:
            cv2.rectangle(frame, (px1, py1), (px2, py2), (0, 0, 255), 2)
            cv2.putText(frame, f'Flagged ID: {person_id}', (px1, py1 - 10),
                        cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0, 0, 255), 2)
        else:
            cv2.rectangle(frame, (px1, py1), (px2, py2), (255, 255, 255), 1)
            cv2.putText(frame, f'Person ID: {person_id}', (px1, py1 - 10),
                        cv2.FONT_HERSHEY_SIMPLEX, 0.5, (255, 255, 255), 1)

    cv2.imshow('Weapon Detection & Re-ID', frame)

    if cv2.waitKey(1) & 0xFF == ord('q'):
        break

cap.release()
cv2.destroyAllWindows()

C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\ultralytics\nn\tasks.py:332: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return torch.load(file, map_location='cpu') 

Successfully loaded imagenet pretrained weights from "C:\Users\ganji/.cache\torch\checkpoints\osnet_x1_0_imagenet.pth"


Ultralytics YOLOv8.0.20  Python-3.9.20 torch-2.5.1 CUDA:0 (NVIDIA GeForce RTX 3050 Laptop GPU, 4096MiB)
Model summary (fused): 168 layers, 11126358 parameters, 0 gradients, 28.4 GFLOPs
Ultralytics YOLOv8.0.20  Python-3.9.20 torch-2.5.1 CUDA:0 (NVIDIA GeForce RTX 3050 Laptop GPU, 4096MiB)
Model summary (fused): 168 layers, 11125971 parameters, 0 gradients, 28.4 GFLOPs
Exception in thread Thread-57:
Traceback (most recent call last):
  File "C:\Users\ganji\anaconda3\envs\torch\lib\threading.py", line 980, in _bootstrap_inner
    self.run()
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\sentry_sdk\integrations\threading.py", line 101, in run
    return _run_old_run_func()
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\sentry_sdk\integrations\threading.py", line 96, in _run_old_run_func
    reraise(*_capture_exception())
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\sentry_sdk\utils.py", line 1723, in reraise
    raise value
  File "C:\Users\ga

In [2]:
# Attempt 1 #
import torch
import torchreid
import cv2
import torchvision.transforms as transforms
from ultralytics import YOLO
import numpy as np
from collections import defaultdict, deque

# Load YOLO models for weapon and person detection
weapon_model = YOLO(r'C:\Users\ganji\Downloads\Weapon 2.v2i.yolov8\runs\detect\train4\weights\best.pt')
person_model = YOLO(r'C:\Users\ganji\Downloads\People Detection.v8i.yolov8\runs\detect\train\weights\best.pt')

# Initialize OSNet re-ID model
reid_model = torchreid.models.build_model('osnet_x1_0', num_classes=1000, pretrained=True)
reid_model.eval()
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
reid_model = reid_model.to(device)

# Transform for re-ID
transform = transforms.Compose([
    transforms.ToPILImage(),
    transforms.Resize((256, 128)),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
])

# Face detection and recognition
faceCascade = cv2.CascadeClassifier("haarcascade_frontalface_default.xml")
clf = cv2.face.LBPHFaceRecognizer_create()
clf.read("classifier.xml")

# Person tracking database
person_database = {}
person_with_weapon = set()
tracked_faces = defaultdict(lambda: {"coords": deque(maxlen=5), "label": "Unknown"})
current_id = 1

def normalize_embedding(features):
    return features / np.linalg.norm(features)

def get_person_id(features, threshold=0.7):
    global current_id
    features = normalize_embedding(features)
    for person_id, data in person_database.items():
        existing_features = normalize_embedding(data['features'])
        similarity = np.dot(features, existing_features)
        if similarity >= threshold:
            return person_id
    person_database[current_id] = {'features': features}
    current_id += 1
    return current_id - 1

def assign_face_label(face_img_gray, confidence_threshold=80):
    face_id, pred = clf.predict(face_img_gray)
    confidence = int(100 * (1 - pred / 300))
    if confidence > confidence_threshold:
        if face_id == 1:
            return "Soldier", (0, 255, 0)  # Green for Soldier
        elif face_id == 2:
            return "Terrorist", (0, 0, 255)  # Red for Terrorist
    return "Unknown", (0, 0, 255)  # Red for Unknown

# Capture video from multiple devices
cap1 = cv2.VideoCapture(0)
cap2 = cv2.VideoCapture(1)

while cap1.isOpened() and cap2.isOpened():
    ret1, frame1 = cap1.read()
    ret2, frame2 = cap2.read()
    if not ret1 or not ret2:
        break

    frames = [frame1, frame2]
    for idx, frame in enumerate(frames):
        weapon_results = weapon_model(frame)
        weapon_boxes = weapon_results[0].boxes.xyxy.cpu().numpy()

        person_results = person_model(frame)
        person_boxes = person_results[0].boxes.xyxy.cpu().numpy()

        for person_box in person_boxes:
            px1, py1, px2, py2 = map(int, person_box[:4])
            person_img = frame[py1:py2, px1:px2]
            person_img_tensor = transform(person_img).unsqueeze(0).to(device)
            with torch.no_grad():
                person_features = reid_model(person_img_tensor).cpu().numpy().flatten()
            person_id = get_person_id(person_features)

            # Update bounding box smoothing
            tracked_faces[person_id]["coords"].append((px1, py1, px2, py2))
            avg_coords = np.mean(tracked_faces[person_id]["coords"], axis=0).astype(int)
            px1, py1, px2, py2 = avg_coords

            gray_face = cv2.cvtColor(frame[py1:py2, px1:px2], cv2.COLOR_BGR2GRAY)
            faces = faceCascade.detectMultiScale(gray_face, 1.3, 6)
            for (x, y, w, h) in faces:
                face_label, face_color = assign_face_label(gray_face[y:y+h, x:x+w])
                tracked_faces[person_id]["label"] = face_label

            if person_id in person_with_weapon:
                label = f'{tracked_faces[person_id]["label"]} (Armed)'
                alert = "THREAT!" if tracked_faces[person_id]["label"] in ["Terrorist", "Unknown"] else "AUTHORIZED"
                cv2.rectangle(frame, (px1, py1), (px2, py2), face_color, 2)
                cv2.putText(frame, label, (px1, py1 - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.5, face_color, 2)
                cv2.putText(frame, alert, (px1, py2 + 20), cv2.FONT_HERSHEY_SIMPLEX, 0.6, face_color, 2)
            else:
                cv2.rectangle(frame, (px1, py1), (px2, py2), (255, 255, 255), 2)

        # Draw weapon bounding boxes and associate weapon with person
        for weapon_box in weapon_boxes:
            wx1, wy1, wx2, wy2 = map(int, weapon_box)
            cv2.rectangle(frame, (wx1, wy1), (wx2, wy2), (0, 0, 255), 2)
            cv2.putText(frame, "Weapon", (wx1, wy1 - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0, 0, 255), 2)

            for person_box in person_boxes:
                px1, py1, px2, py2 = map(int, person_box[:4])
                if wx1 < px2 and wx2 > px1 and wy1 < py2 and wy2 > py1:  # Overlap
                    person_with_weapon.add(person_id)

        cv2.imshow(f'Camera {idx+1}', frame)

    if cv2.waitKey(1) & 0xFF == ord('q'):
        break

cap1.release()
cap2.release()
cv2.destroyAllWindows()

Successfully loaded imagenet pretrained weights from "C:\Users\ganji/.cache\torch\checkpoints\osnet_x1_0_imagenet.pth"


Ultralytics YOLOv8.0.20  Python-3.9.20 torch-2.5.1 CUDA:0 (NVIDIA GeForce RTX 3050 Laptop GPU, 4096MiB)
Model summary (fused): 168 layers, 11126358 parameters, 0 gradients, 28.4 GFLOPs
Ultralytics YOLOv8.0.20  Python-3.9.20 torch-2.5.1 CUDA:0 (NVIDIA GeForce RTX 3050 Laptop GPU, 4096MiB)
Model summary (fused): 168 layers, 11125971 parameters, 0 gradients, 28.4 GFLOPs


In [14]:
# Attempt 2 #
import torch
import torchreid
import cv2
import torchvision.transforms as transforms
from ultralytics import YOLO
import numpy as np
from collections import defaultdict, deque

# Load YOLO models for weapon and person detection
weapon_model = YOLO(r'C:\Users\ganji\Downloads\Weapon 2.v2i.yolov8\runs\detect\train4\weights\best.pt')
person_model = YOLO(r'C:\Users\ganji\Downloads\People Detection.v8i.yolov8\runs\detect\train\weights\best.pt')

# Initialize OSNet re-ID model
reid_model = torchreid.models.build_model('osnet_x1_0', num_classes=1000, pretrained=True)
reid_model.eval()
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
reid_model = reid_model.to(device)

# Transform for re-ID
transform = transforms.Compose([
    transforms.ToPILImage(),
    transforms.Resize((256, 128)),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
])

# Face detection and recognition
faceCascade = cv2.CascadeClassifier("haarcascade_frontalface_default.xml")
clf = cv2.face.LBPHFaceRecognizer_create()
clf.read("classifier.xml")

# Person tracking database
person_database = {}
person_with_weapon = set()
tracked_faces = defaultdict(lambda: {"coords": deque(maxlen=5), "label": "Unknown"})
current_id = 1

# Normalize embedding for person matching
def normalize_embedding(features):
    return features / np.linalg.norm(features)

# Identify person using re-ID embeddings
def get_person_id(features, threshold=0.6):
    global current_id
    features = normalize_embedding(features)
    best_match_id = None
    highest_similarity = 0
    
    for person_id, data in person_database.items():
        existing_features = normalize_embedding(data['features'])
        similarity = np.dot(features, existing_features)
        if similarity >= threshold and similarity > highest_similarity:
            highest_similarity = similarity
            best_match_id = person_id
    
    if best_match_id is not None:
        return best_match_id
    else:
        # Assign a new ID if no match found
        person_database[current_id] = {'features': features}
        current_id += 1
        return current_id - 1

# Assign label to a face based on classifier
def assign_face_label(face_img_gray, confidence_threshold=70):
    face_id, pred = clf.predict(face_img_gray)
    confidence = int(100 * (1 - pred / 300))
    if confidence >= confidence_threshold:
        if face_id == 1:
            return "Soldier", (0, 255, 0)  # Green for Soldier
        elif face_id == 2:
            return "Terrorist", (0, 0, 255)  # Red for Terrorist
    return "Unknown", (255, 0, 0)  # Blue for Unknown

# Capture video from multiple devices
cap1 = cv2.VideoCapture(0)
cap2 = cv2.VideoCapture(1)

while cap1.isOpened() and cap2.isOpened():
    ret1, frame1 = cap1.read()
    ret2, frame2 = cap2.read()
    if not ret1 or not ret2:
        break

    frames = [frame1, frame2]
    for idx, frame in enumerate(frames):
        weapon_results = weapon_model(frame)
        weapon_boxes = weapon_results[0].boxes.xyxy.cpu().numpy()

        person_results = person_model(frame)
        person_boxes = person_results[0].boxes.xyxy.cpu().numpy()

        for person_box in person_boxes:
            px1, py1, px2, py2 = map(int, person_box[:4])
            person_img = frame[py1:py2, px1:px2]
            person_img_tensor = transform(person_img).unsqueeze(0).to(device)
            with torch.no_grad():
                person_features = reid_model(person_img_tensor).cpu().numpy().flatten()
            person_id = get_person_id(person_features)

            # Update bounding box smoothing
            tracked_faces[person_id]["coords"].append((px1, py1, px2, py2))
            avg_coords = np.mean(tracked_faces[person_id]["coords"], axis=0).astype(int)
            px1, py1, px2, py2 = avg_coords

            gray_face = cv2.cvtColor(frame[py1:py2, px1:px2], cv2.COLOR_BGR2GRAY)
            faces = faceCascade.detectMultiScale(gray_face, 1.3, 6)
            for (x, y, w, h) in faces:
                face_label, face_color = assign_face_label(gray_face[y:y+h, x:x+w])
                tracked_faces[person_id]["label"] = face_label

            # Debug: Print detected label
            print(f"Person ID {person_id}: Detected label = {tracked_faces[person_id]['label']}")

            if person_id in person_with_weapon:
                label = f'{tracked_faces[person_id]["label"]} (Armed)'
                alert = "THREAT!" if tracked_faces[person_id]["label"] in ["Terrorist", "Unknown"] else "AUTHORIZED"
                cv2.rectangle(frame, (px1, py1), (px2, py2), face_color, 2)
                cv2.putText(frame, label, (px1, py1 - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.5, face_color, 2)
                cv2.putText(frame, alert, (px1, py2 + 20), cv2.FONT_HERSHEY_SIMPLEX, 0.6, face_color, 2)
            else:
                label = tracked_faces[person_id]["label"]
                cv2.rectangle(frame, (px1, py1), (px2, py2), face_color, 2)
                cv2.putText(frame, label, (px1, py1 - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.5, face_color, 2)

        # Draw weapon bounding boxes and associate weapon with persons
        for weapon_box in weapon_boxes:
            wx1, wy1, wx2, wy2 = map(int, weapon_box)
            cv2.rectangle(frame, (wx1, wy1), (wx2, wy2), (0, 0, 255), 2)
            cv2.putText(frame, "Weapon", (wx1, wy1 - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0, 0, 255), 2)

            for person_box in person_boxes:
                px1, py1, px2, py2 = map(int, person_box[:4])
                if wx1 < px2 and wx2 > px1 and wy1 < py2 and wy2 > py1:  # Overlap
                    person_with_weapon.add(person_id)

        cv2.imshow(f'Camera {idx+1}', frame)

    if cv2.waitKey(1) & 0xFF == ord('q'):
        break

cap1.release()
cap2.release()
cv2.destroyAllWindows()

C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\ultralytics\nn\tasks.py:332: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return torch.load(file, map_location='cpu') 

Successfully loaded imagenet pretrained weights from "C:\Users\ganji/.cache\torch\checkpoints\osnet_x1_0_imagenet.pth"


Ultralytics YOLOv8.0.20  Python-3.9.20 torch-2.5.1 CUDA:0 (NVIDIA GeForce RTX 3050 Laptop GPU, 4096MiB)
Model summary (fused): 168 layers, 11126358 parameters, 0 gradients, 28.4 GFLOPs
Ultralytics YOLOv8.0.20  Python-3.9.20 torch-2.5.1 CUDA:0 (NVIDIA GeForce RTX 3050 Laptop GPU, 4096MiB)
Model summary (fused): 168 layers, 11125971 parameters, 0 gradients, 28.4 GFLOPs


Person ID 1: Detected label = Unknown
Person ID 2: Detected label = Unknown
Person ID 2: Detected label = Unknown
Person ID 1: Detected label = Unknown
Person ID 2: Detected label = Unknown
Person ID 1: Detected label = Soldier
Person ID 1: Detected label = Soldier
Person ID 1: Detected label = Soldier
Person ID 2: Detected label = Unknown
Person ID 1: Detected label = Soldier
Person ID 1: Detected label = Soldier
Person ID 1: Detected label = Soldier
Person ID 2: Detected label = Unknown
Person ID 1: Detected label = Soldier
Person ID 2: Detected label = Unknown
Person ID 1: Detected label = Terrorist
Person ID 2: Detected label = Unknown
Person ID 2: Detected label = Unknown
Person ID 1: Detected label = Terrorist
Person ID 2: Detected label = Unknown
Person ID 1: Detected label = Terrorist
Person ID 2: Detected label = Unknown
Person ID 1: Detected label = Terrorist
Person ID 2: Detected label = Unknown
Person ID 1: Detected label = Terrorist
Person ID 2: Detected label = Unknown
Pe

In [8]:
# Different Thresholds #
import torch
import torchreid
import cv2
import torchvision.transforms as transforms
from ultralytics import YOLO
import numpy as np
from collections import defaultdict, deque

# Load YOLO models for weapon and person detection
weapon_model = YOLO(r'C:\Users\ganji\Downloads\Weapon 2.v2i.yolov8\runs\detect\train4\weights\best.pt')
person_model = YOLO(r'C:\Users\ganji\Downloads\People Detection.v8i.yolov8\runs\detect\train\weights\best.pt')

# Initialize OSNet re-ID model
reid_model = torchreid.models.build_model('osnet_x1_0', num_classes=1000, pretrained=True)
reid_model.eval()
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
reid_model = reid_model.to(device)

# Transform for re-ID
transform = transforms.Compose([
    transforms.ToPILImage(),
    transforms.Resize((256, 128)),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
])

# Load the face cascade for face detection
faceCascade = cv2.CascadeClassifier("haarcascade_frontalface_default.xml")
clf = cv2.face.LBPHFaceRecognizer_create()
clf.read("classifier.xml")

# Person tracking database
person_database = {}
person_with_weapon = set()
tracked_faces = defaultdict(lambda: {
    "coords": deque(maxlen=5),
    "label": "Unknown",
    "history": deque(maxlen=5)  # To smooth the label transitions
})
current_id = 1

# Define colors for different labels
colors = {
    "Soldier": (0, 255, 0),       # Green
    "Terrorist": (0, 0, 255),     # Red
    "Unknown": (255, 255, 255),   # White
    "Armed": (255, 255, 0)        # Cyan
}

# Confidence thresholds for each class
confidence_thresholds = {
    "Soldier": 70,
    "Terrorist": 80,
    "Unknown": 70
}

def normalize_embedding(features):
    return features / np.linalg.norm(features)

def get_person_id(features, threshold=0.75):
    global current_id
    features = normalize_embedding(features)
    for person_id, data in person_database.items():
        existing_features = normalize_embedding(data['features'])
        similarity = np.dot(features, existing_features)
        if similarity >= threshold:
            return person_id
    person_database[current_id] = {'features': features}
    current_id += 1
    return current_id - 1

def assign_face_label(face_img_gray, confidence_threshold):
    face_id, pred = clf.predict(face_img_gray)
    confidence = int(100 * (1 - pred / 300))
    if confidence >= confidence_threshold:
        if face_id == 1:
            return "Soldier", colors["Soldier"]
        elif face_id == 2:
            return "Terrorist", colors["Terrorist"]
    return "Unknown", colors["Unknown"]

# Capture video from multiple devices
cap1 = cv2.VideoCapture(0)
cap2 = cv2.VideoCapture(1)

while cap1.isOpened() and cap2.isOpened():
    ret1, frame1 = cap1.read()
    ret2, frame2 = cap2.read()
    if not ret1 or not ret2:
        break

    frames = [frame1, frame2]
    for idx, frame in enumerate(frames):
        weapon_results = weapon_model(frame)
        weapon_boxes = weapon_results[0].boxes.xyxy.cpu().numpy()

        person_results = person_model(frame)
        person_boxes = person_results[0].boxes.xyxy.cpu().numpy()

        for person_box in person_boxes:
            px1, py1, px2, py2 = map(int, person_box[:4])
            person_img = frame[py1:py2, px1:px2]
            if person_img.size == 0:
                continue  # Skip empty frames

            person_img_tensor = transform(person_img).unsqueeze(0).to(device)
            with torch.no_grad():
                person_features = reid_model(person_img_tensor).cpu().numpy().flatten()
            person_id = get_person_id(person_features)

            # Update bounding box smoothing
            tracked_faces[person_id]["coords"].append((px1, py1, px2, py2))
            avg_coords = np.mean(tracked_faces[person_id]["coords"], axis=0).astype(int)
            px1, py1, px2, py2 = avg_coords

            gray_face = cv2.cvtColor(frame[py1:py2, px1:px2], cv2.COLOR_BGR2GRAY)
            face_label, face_color = assign_face_label(
                gray_face,
                confidence_threshold=confidence_thresholds.get("Soldier" if tracked_faces[person_id]["label"] == "Soldier" else "Terrorist", confidence_thresholds["Unknown"])
            )

            # Update the label history for smoother transitions
            tracked_faces[person_id]["history"].append(face_label)
            most_common_label = max(set(tracked_faces[person_id]["history"]), key=tracked_faces[person_id]["history"].count)
            tracked_faces[person_id]["label"] = most_common_label

            # Check if person is armed
            if person_id in person_with_weapon:
                label = f'{tracked_faces[person_id]["label"]} (Armed)'
                alert = "THREAT!" if tracked_faces[person_id]["label"] == "Terrorist" else "AUTHORIZED"
                cv2.rectangle(frame, (px1, py1), (px2, py2), face_color, 2)
                cv2.putText(frame, label, (px1, py1 - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.5, face_color, 2)
                cv2.putText(frame, alert, (px1, py2 + 20), cv2.FONT_HERSHEY_SIMPLEX, 0.6, face_color, 2)
            else:
                if tracked_faces[person_id]["label"] == "Unknown":
                    label = f'ID: {person_id} {tracked_faces[person_id]["label"]}'
                else:
                    label = f'{tracked_faces[person_id]["label"]}'
                cv2.rectangle(frame, (px1, py1), (px2, py2), face_color, 2)
                cv2.putText(frame, label, (px1, py1 - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.5, face_color, 2)

        # Draw weapon bounding boxes and associate weapon with person
        for weapon_box in weapon_boxes:
            wx1, wy1, wx2, wy2 = map(int, weapon_box)
            cv2.rectangle(frame, (wx1, wy1), (wx2, wy2), (0, 0, 255), 2)
            cv2.putText(frame, "Weapon", (wx1, wy1 - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0, 0, 255), 2)

            for person_box in person_boxes:
                px1, py1, px2, py2 = map(int, person_box[:4])
                if wx1 < px2 and wx2 > px1 and wy1 < py2 and wy2 > py1:  # Overlap check
                    person_with_weapon.add(person_id)

        cv2.imshow(f'Camera {idx+1}', frame)

    if cv2.waitKey(1) & 0xFF == ord('q'):
        break

cap1.release()
cap2.release()
cv2.destroyAllWindows()

C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\ultralytics\nn\tasks.py:332: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return torch.load(file, map_location='cpu') 

Successfully loaded imagenet pretrained weights from "C:\Users\ganji/.cache\torch\checkpoints\osnet_x1_0_imagenet.pth"


Ultralytics YOLOv8.0.20  Python-3.9.20 torch-2.5.1 CUDA:0 (NVIDIA GeForce RTX 3050 Laptop GPU, 4096MiB)
Model summary (fused): 168 layers, 11126358 parameters, 0 gradients, 28.4 GFLOPs
Ultralytics YOLOv8.0.20  Python-3.9.20 torch-2.5.1 CUDA:0 (NVIDIA GeForce RTX 3050 Laptop GPU, 4096MiB)
Model summary (fused): 168 layers, 11125971 parameters, 0 gradients, 28.4 GFLOPs


In [13]:
import torch
import torchreid
import cv2
import torchvision.transforms as transforms
from ultralytics import YOLO
import numpy as np

# Load YOLO models for weapon and person detection
weapon_model = YOLO(r'C:\Users\ganji\Downloads\Weapon 2.v2i.yolov8\runs\detect\train4\weights\best.pt')
person_model = YOLO(r'C:\Users\ganji\Downloads\People Detection.v8i.yolov8\runs\detect\train\weights\best.pt')

# Initialize OSNet re-ID model
reid_model = torchreid.models.build_model('osnet_x1_0', num_classes=1000, pretrained=True)
reid_model.eval()
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
reid_model = reid_model.to(device)

# Transform for re-ID
transform = transforms.Compose([
    transforms.ToPILImage(),
    transforms.Resize((256, 128)),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
])

# Face detection and recognition
faceCascade = cv2.CascadeClassifier("haarcascade_frontalface_default.xml")
clf = cv2.face.LBPHFaceRecognizer_create()
clf.read("classifier.xml")

# Person tracking database
person_database = {}
person_with_weapon = set()
current_id = 1
flagged_ids = set()  # IDs for flagged individuals (Unknown with weapon or Terrorist)

# Normalize embedding for person matching
def normalize_embedding(features):
    return features / np.linalg.norm(features)

# Identify person using re-ID embeddings
def get_person_id(features, threshold=0.6):
    global current_id
    features = normalize_embedding(features)
    best_match_id = None
    highest_similarity = 0
    
    for person_id, data in person_database.items():
        existing_features = normalize_embedding(data['features'])
        similarity = np.dot(features, existing_features)
        if similarity >= threshold and similarity > highest_similarity:
            highest_similarity = similarity
            best_match_id = person_id
    
    if best_match_id is not None:
        return best_match_id
    else:
        # Assign a new ID if no match found
        person_database[current_id] = {'features': features}
        current_id += 1
        return current_id - 1

# Assign label to a face based on classifier
def assign_face_label(face_img_gray, confidence_threshold=70):
    face_id, pred = clf.predict(face_img_gray)
    confidence = int(100 * (1 - pred / 300))
    if confidence >= confidence_threshold:
        if face_id == 1:
            return "Soldier"
        elif face_id == 2:
            return "Terrorist"
    return "Unknown"

# Capture video from multiple devices
cap1 = cv2.VideoCapture(0)
cap2 = cv2.VideoCapture(1)

while cap1.isOpened() and cap2.isOpened():
    ret1, frame1 = cap1.read()
    ret2, frame2 = cap2.read()
    if not ret1 or not ret2:
        break

    frames = [frame1, frame2]
    for idx, frame in enumerate(frames):
        weapon_results = weapon_model(frame, conf=0.5, iou=0.4)
        weapon_boxes = weapon_results[0].boxes.xyxy.cpu().numpy()

        person_results = person_model(frame, conf=0.5, iou=0.4)
        person_boxes = person_results[0].boxes.xyxy.cpu().numpy()

        for person_box in person_boxes:
            px1, py1, px2, py2 = map(int, person_box[:4])
            person_img = frame[py1:py2, px1:px2]
            person_img_tensor = transform(person_img).unsqueeze(0).to(device)
            with torch.no_grad():
                person_features = reid_model(person_img_tensor).cpu().numpy().flatten()
            person_id = get_person_id(person_features)

            gray_face = cv2.cvtColor(frame[py1:py2, px1:px2], cv2.COLOR_BGR2GRAY)
            faces = faceCascade.detectMultiScale(gray_face, 1.3, 6)
            label = "Unknown"
            for (x, y, w, h) in faces:
                label = assign_face_label(gray_face[y:y+h, x:x+w])
            
            if label == "Terrorist":
                flagged_ids.add(person_id)

            # Check if the person is armed
            is_armed = False
            for weapon_box in weapon_boxes:
                wx1, wy1, wx2, wy2 = map(int, weapon_box)
                if wx1 < px2 and wx2 > px1 and wy1 < py2 and wy2 > py1:
                    is_armed = True
                    person_with_weapon.add(person_id)
            
            if is_armed and label == "Unknown":
                flagged_ids.add(person_id)

            # Draw bounding boxes only for flagged individuals
            if person_id in flagged_ids:
                if is_armed:
                    label += " Armed"
                color = (0, 0, 255) if "Terrorist" in label else (255, 165, 0)
                cv2.rectangle(frame, (px1, py1), (px2, py2), color, 2)
                cv2.putText(frame, f"ID: {person_id}, {label}", (px1, py1 - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.5, color, 2)

        # Draw weapon bounding boxes
        for weapon_box in weapon_boxes:
            wx1, wy1, wx2, wy2 = map(int, weapon_box)
            cv2.rectangle(frame, (wx1, wy1), (wx2, wy2), (0, 0, 255), 2)
            cv2.putText(frame, "Weapon", (wx1, wy1 - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0, 0, 255), 2)

        cv2.imshow(f'Camera {idx+1}', frame)

    if cv2.waitKey(1) & 0xFF == ord('q'):
        break

cap1.release()
cap2.release()
cv2.destroyAllWindows()

C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\ultralytics\nn\tasks.py:332: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return torch.load(file, map_location='cpu') 

Successfully loaded imagenet pretrained weights from "C:\Users\ganji/.cache\torch\checkpoints\osnet_x1_0_imagenet.pth"


Ultralytics YOLOv8.0.20  Python-3.9.20 torch-2.5.1 CUDA:0 (NVIDIA GeForce RTX 3050 Laptop GPU, 4096MiB)
Model summary (fused): 168 layers, 11126358 parameters, 0 gradients, 28.4 GFLOPs
Ultralytics YOLOv8.0.20  Python-3.9.20 torch-2.5.1 CUDA:0 (NVIDIA GeForce RTX 3050 Laptop GPU, 4096MiB)
Model summary (fused): 168 layers, 11125971 parameters, 0 gradients, 28.4 GFLOPs


In [2]:
# Final Code #
import torch
import torchreid
import cv2
import torchvision.transforms as transforms
from ultralytics import YOLO
import numpy as np

# Load YOLO models for weapon and person detection
weapon_model = YOLO(r'C:\Users\ganji\Downloads\Weapon 2.v2i.yolov8\runs\detect\train4\weights\best.pt')
person_model = YOLO(r'C:\Users\ganji\Downloads\People Detection.v8i.yolov8\runs\detect\train\weights\best.pt')

# Initialize OSNet re-ID model
reid_model = torchreid.models.build_model('osnet_x1_0', num_classes=1000, pretrained=True)
reid_model.eval()
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
reid_model = reid_model.to(device)

# Transform for re-ID
transform = transforms.Compose([
    transforms.ToPILImage(),
    transforms.Resize((256, 128)),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
])

# Face detection and recognition
faceCascade = cv2.CascadeClassifier("haarcascade_frontalface_default.xml")
clf = cv2.face.LBPHFaceRecognizer_create()
clf.read("classifier.xml")

# Person tracking database
person_database = {}
person_with_weapon = set()
current_id = 1
flagged_ids = set()  # IDs for flagged individuals (Unknown with weapon or Terrorist)

# Normalize embedding for person matching
def normalize_embedding(features):
    return features / np.linalg.norm(features)

# Identify person using re-ID embeddings
def get_person_id(features, threshold=0.6):
    global current_id
    features = normalize_embedding(features)
    best_match_id = None
    highest_similarity = 0
    
    for person_id, data in person_database.items():
        existing_features = normalize_embedding(data['features'])
        similarity = np.dot(features, existing_features)
        if similarity >= threshold and similarity > highest_similarity:
            highest_similarity = similarity
            best_match_id = person_id
    
    if best_match_id is not None:
        return best_match_id
    else:
        # Assign a new ID if no match found
        person_database[current_id] = {'features': features}
        current_id += 1
        return current_id - 1

# Assign label to a face based on classifier
def assign_face_label(face_img_gray, confidence_threshold=70):
    face_id, pred = clf.predict(face_img_gray)
    confidence = int(100 * (1 - pred / 300))
    if confidence >= confidence_threshold:
        if face_id == 1:
            return "Soldier"
        elif face_id == 2:
            return "Terrorist"
    return "Unknown"

# Capture video from multiple devices
cap1 = cv2.VideoCapture(0)
cap2 = cv2.VideoCapture(1)

while cap1.isOpened() and cap2.isOpened():
    ret1, frame1 = cap1.read()
    ret2, frame2 = cap2.read()
    if not ret1 or not ret2:
        break

    frames = [frame1, frame2]
    for idx, frame in enumerate(frames):
        weapon_results = weapon_model(frame, conf=0.5, iou=0.4)
        weapon_boxes = weapon_results[0].boxes.xyxy.cpu().numpy()

        person_results = person_model(frame, conf=0.5, iou=0.4)
        person_boxes = person_results[0].boxes.xyxy.cpu().numpy()

        for person_box in person_boxes:
            px1, py1, px2, py2 = map(int, person_box[:4])
            person_img = frame[py1:py2, px1:px2]
            person_img_tensor = transform(person_img).unsqueeze(0).to(device)
            with torch.no_grad():
                person_features = reid_model(person_img_tensor).cpu().numpy().flatten()
            person_id = get_person_id(person_features)

            gray_face = cv2.cvtColor(frame[py1:py2, px1:px2], cv2.COLOR_BGR2GRAY)
            faces = faceCascade.detectMultiScale(gray_face, 1.3, 6)
            label = "Unknown"
            for (x, y, w, h) in faces:
                label = assign_face_label(gray_face[y:y+h, x:x+w])
            
            if label == "Terrorist":
                flagged_ids.add(person_id)

            # Check if the person is armed
            is_armed = False
            for weapon_box in weapon_boxes:
                wx1, wy1, wx2, wy2 = map(int, weapon_box)
                if wx1 < px2 and wx2 > px1 and wy1 < py2 and wy2 > py1:
                    is_armed = True
                    person_with_weapon.add(person_id)
            
            if is_armed and label == "Unknown":
                flagged_ids.add(person_id)

            # Draw bounding boxes only for flagged individuals
            if person_id in flagged_ids:
                if is_armed:
                    label += " Armed"
                color = (0, 0, 255) if "Terrorist" in label else (255, 165, 0)
                cv2.rectangle(frame, (px1, py1), (px2, py2), color, 2)
                cv2.putText(frame, f"ID: {person_id}, {label}", (px1, py1 - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.5, color, 2)

        # Draw weapon bounding boxes
        for weapon_box in weapon_boxes:
            wx1, wy1, wx2, wy2 = map(int, weapon_box)
            cv2.rectangle(frame, (wx1, wy1), (wx2, wy2), (0, 0, 255), 2)
            cv2.putText(frame, "Weapon", (wx1, wy1 - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0, 0, 255), 2)

        cv2.imshow(f'Camera {idx+1}', frame)

    if cv2.waitKey(1) & 0xFF == ord('q'):
        break

cap1.release()
cap2.release()
cv2.destroyAllWindows()

C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\ultralytics\nn\tasks.py:332: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return torch.load(file, map_location='cpu') 

Successfully loaded imagenet pretrained weights from "C:\Users\ganji/.cache\torch\checkpoints\osnet_x1_0_imagenet.pth"


Ultralytics YOLOv8.0.20  Python-3.9.20 torch-2.5.1 CUDA:0 (NVIDIA GeForce RTX 3050 Laptop GPU, 4096MiB)
Model summary (fused): 168 layers, 11126358 parameters, 0 gradients, 28.4 GFLOPs
Ultralytics YOLOv8.0.20  Python-3.9.20 torch-2.5.1 CUDA:0 (NVIDIA GeForce RTX 3050 Laptop GPU, 4096MiB)
Model summary (fused): 168 layers, 11125971 parameters, 0 gradients, 28.4 GFLOPs


In [1]:
import torch
import torchreid
import cv2
import torchvision.transforms as transforms
from ultralytics import YOLO
import numpy as np
from collections import defaultdict, deque
import time
import tkinter as tk
from PIL import Image, ImageTk
import threading

# Load YOLO models for weapon and person detection
weapon_model = YOLO(r'C:\Users\ganji\Downloads\Weapon 2.v2i.yolov8\runs\detect\train4\weights\best.pt')
person_model = YOLO(r'C:\Users\ganji\Downloads\People Detection.v8i.yolov8\runs\detect\train\weights\best.pt')

# Initialize OSNet re-ID model
reid_model = torchreid.models.build_model('osnet_x1_0', num_classes=1000, pretrained=True)
reid_model.eval()
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
reid_model = reid_model.to(device)

# Transform for re-ID
transform = transforms.Compose([
    transforms.ToPILImage(),
    transforms.Resize((256, 128)),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
])

# Face detection and recognition
faceCascade = cv2.CascadeClassifier("haarcascade_frontalface_default.xml")
clf = cv2.face.LBPHFaceRecognizer_create()
clf.read("classifier.xml")

# Person tracking database
person_database = {}
person_with_weapon = set()
tracked_faces = defaultdict(lambda: {"coords": deque(maxlen=5), "label": "Unknown", "last_alert_time": 0})
current_id = 1

# Time gap for alerting and pop-up notifications
alert_interval = 10  # Time in seconds between alerts for each person

# Function to normalize embeddings
def normalize_embedding(features):
    return features / np.linalg.norm(features)

# Identify person using re-ID embeddings
def get_person_id(features, threshold=0.6):
    global current_id
    features = normalize_embedding(features)
    best_match_id = None
    highest_similarity = 0
    
    for person_id, data in person_database.items():
        existing_features = normalize_embedding(data['features'])
        similarity = np.dot(features, existing_features)
        if similarity >= threshold and similarity > highest_similarity:
            highest_similarity = similarity
            best_match_id = person_id
    
    if best_match_id is not None:
        return best_match_id
    else:
        # Assign a new ID if no match found
        person_database[current_id] = {'features': features}
        current_id += 1
        return current_id - 1

# Assign label to a face based on classifier
def assign_face_label(face_img_gray, confidence_threshold=70):
    face_id, pred = clf.predict(face_img_gray)
    confidence = int(100 * (1 - pred / 300))
    if confidence >= confidence_threshold:
        if face_id == 1:
            return "Soldier", (0, 255, 0)  # Green for Soldier
        elif face_id == 2:
            return "Terrorist", (0, 0, 255)  # Red for Terrorist
    return "Unknown", (255, 0, 0)  # Blue for Unknown

# Function to show a popup warning
def show_popup(person_image):
    popup = tk.Tk()
    popup.title("Warning: Possible Threat Detected")
    popup.geometry("300x400")
    tk.Label(popup, text="Threat Detected!", font=("Helvetica", 16), fg="red").pack(pady=10)

    if person_image is not None:
        person_img_pil = Image.fromarray(person_image)
        person_img_pil.thumbnail((250, 250))
        img_tk = ImageTk.PhotoImage(person_img_pil)
        img_label = tk.Label(popup, image=img_tk)
        img_label.image = img_tk
        img_label.pack(pady=10)

    tk.Button(popup, text="OK", command=popup.destroy).pack(pady=10)
    popup.mainloop()

# Trigger the popup notification in a new thread
def trigger_popup(person_image):
    threading.Thread(target=show_popup, args=(person_image,)).start()

# Capture video from multiple devices
cap1 = cv2.VideoCapture(0)
cap2 = cv2.VideoCapture(1)

while cap1.isOpened() and cap2.isOpened():
    ret1, frame1 = cap1.read()
    ret2, frame2 = cap2.read()
    if not ret1 or not ret2:
        break

    frames = [frame1, frame2]
    for idx, frame in enumerate(frames):
        weapon_results = weapon_model(frame)
        weapon_boxes = weapon_results[0].boxes.xyxy.cpu().numpy()

        person_results = person_model(frame)
        person_boxes = person_results[0].boxes.xyxy.cpu().numpy()

        for person_box in person_boxes:
            px1, py1, px2, py2 = map(int, person_box[:4])
            person_img = frame[py1:py2, px1:px2]
            person_img_tensor = transform(person_img).unsqueeze(0).to(device)
            with torch.no_grad():
                person_features = reid_model(person_img_tensor).cpu().numpy().flatten()
            person_id = get_person_id(person_features)

            # Update bounding box smoothing
            tracked_faces[person_id]["coords"].append((px1, py1, px2, py2))
            avg_coords = np.mean(tracked_faces[person_id]["coords"], axis=0).astype(int)
            px1, py1, px2, py2 = avg_coords

            gray_face = cv2.cvtColor(frame[py1:py2, px1:px2], cv2.COLOR_BGR2GRAY)
            faces = faceCascade.detectMultiScale(gray_face, 1.3, 6)
            for (x, y, w, h) in faces:
                face_label, face_color = assign_face_label(gray_face[y:y+h, x:x+w])
                tracked_faces[person_id]["label"] = face_label

            # If a person with a weapon is detected as "Terrorist" or "Unknown", trigger warning
            if person_id in person_with_weapon:
                label = f'{tracked_faces[person_id]["label"]} (Armed)'
                
                current_time = time.time()
                if current_time - tracked_faces[person_id]["last_alert_time"] >= alert_interval:
                    if tracked_faces[person_id]["label"] in ["Unknown", "Terrorist"]:
                        tracked_faces[person_id]["last_alert_time"] = current_time
                        print(f"Alert: Person ID {person_id} detected with weapon.")
                        trigger_popup(person_img)  # Show popup notification

                # Display warning on the screen
                cv2.rectangle(frame, (px1, py1), (px2, py2), (0, 0, 255), 2)
                cv2.putText(frame, label, (px1, py1 - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.5, face_color, 2)
            else:
                label = tracked_faces[person_id]["label"]
                cv2.rectangle(frame, (px1, py1), (px2, py2), face_color, 2)
                cv2.putText(frame, label, (px1, py1 - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.5, face_color, 2)

        # Draw weapon bounding boxes and associate weapon with persons
        for weapon_box in weapon_boxes:
            wx1, wy1, wx2, wy2 = map(int, weapon_box)
            cv2.rectangle(frame, (wx1, wy1), (wx2, wy2), (0, 0, 255), 2)
            cv2.putText(frame, "Weapon", (wx1, wy1 - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0, 0, 255), 2)

            for person_box in person_boxes:
                px1, py1, px2, py2 = map(int, person_box[:4])
                if wx1 < px2 and wx2 > px1 and wy1 < py2 and wy2 > py1:  # Overlap
                    person_with_weapon.add(person_id)

        cv2.imshow(f'Camera {idx+1}', frame)

    if cv2.waitKey(1) & 0xFF == ord('q'):
        break

cap1.release()
cap2.release()
cv2.destroyAllWindows()

C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\torchreid\reid\metrics\rank.py:11: UserWarning: Cython evaluation (very fast so highly recommended) is unavailable, now use python evaluation.
  warnings.warn(
C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\ultralytics\nn\tasks.py:332: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weight

Successfully loaded imagenet pretrained weights from "C:\Users\ganji/.cache\torch\checkpoints\osnet_x1_0_imagenet.pth"


Ultralytics YOLOv8.0.20  Python-3.9.20 torch-2.5.1 CUDA:0 (NVIDIA GeForce RTX 3050 Laptop GPU, 4096MiB)
Model summary (fused): 168 layers, 11126358 parameters, 0 gradients, 28.4 GFLOPs
Ultralytics YOLOv8.0.20  Python-3.9.20 torch-2.5.1 CUDA:0 (NVIDIA GeForce RTX 3050 Laptop GPU, 4096MiB)
Model summary (fused): 168 layers, 11125971 parameters, 0 gradients, 28.4 GFLOPs


Alert: Person ID 4 detected with weapon.
Alert: Person ID 2 detected with weapon.


Exception in thread Thread-10:
Traceback (most recent call last):
  File "C:\Users\ganji\anaconda3\envs\torch\lib\threading.py", line 980, in _bootstrap_inner
    self.run()
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\sentry_sdk\integrations\threading.py", line 101, in run
    return _run_old_run_func()
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\sentry_sdk\integrations\threading.py", line 96, in _run_old_run_func
    reraise(*_capture_exception())
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\sentry_sdk\utils.py", line 1723, in reraise
    raise value
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\sentry_sdk\integrations\threading.py", line 94, in _run_old_run_func
    return old_run_func(self, *a, **kw)
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\ipykernel\ipkernel.py", line 766, in run_closure
    _threading_Thread_run(self)
  File "C:\Users\ganji\anaconda3\envs\torch\lib\threading.py", line 917, in

Alert: Person ID 3 detected with weapon.
Alert: Person ID 5 detected with weapon.
Alert: Person ID 3 detected with weapon.
Alert: Person ID 6 detected with weapon.


Exception in thread Thread-21:
Traceback (most recent call last):
  File "C:\Users\ganji\anaconda3\envs\torch\lib\threading.py", line 980, in _bootstrap_inner
    self.run()
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\sentry_sdk\integrations\threading.py", line 101, in run
    return _run_old_run_func()
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\sentry_sdk\integrations\threading.py", line 96, in _run_old_run_func
    reraise(*_capture_exception())
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\sentry_sdk\utils.py", line 1723, in reraise
    raise value
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\sentry_sdk\integrations\threading.py", line 94, in _run_old_run_func
    return old_run_func(self, *a, **kw)
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\ipykernel\ipkernel.py", line 766, in run_closure
    _threading_Thread_run(self)
  File "C:\Users\ganji\anaconda3\envs\torch\lib\threading.py", line 917, in

Alert: Person ID 7 detected with weapon.


In [ ]:
import torch
import torchreid
import cv2
import torchvision.transforms as transforms
from ultralytics import YOLO
import numpy as np
from collections import defaultdict, deque
import time
import tkinter as tk
from PIL import Image, ImageTk
import threading

# Load YOLO models for weapon and person detection
weapon_model = YOLO(r'C:\Users\ganji\Downloads\Weapon 2.v2i.yolov8\runs\detect\train4\weights\best.pt')
person_model = YOLO(r'C:\Users\ganji\Downloads\People Detection.v8i.yolov8\runs\detect\train\weights\best.pt')

# Initialize OSNet re-ID model
reid_model = torchreid.models.build_model('osnet_x1_0', num_classes=1000, pretrained=True)
reid_model.eval()
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
reid_model = reid_model.to(device)

# Transform for re-ID
transform = transforms.Compose([
    transforms.ToPILImage(),
    transforms.Resize((256, 128)),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
])

# Face detection and recognition
faceCascade = cv2.CascadeClassifier("haarcascade_frontalface_default.xml")
clf = cv2.face.LBPHFaceRecognizer_create()
clf.read("classifier.xml")

# Person tracking database
person_database = {}
person_with_weapon = set()
tracked_faces = defaultdict(lambda: {"coords": deque(maxlen=5), "label": "Unknown", "last_alert_time": 0})
current_id = 1

# Time gap for alerting and pop-up notifications
alert_interval = 10  # Time in seconds between alerts for each person

# Function to normalize embeddings
def normalize_embedding(features):
    return features / np.linalg.norm(features)

# Identify person using re-ID embeddings
def get_person_id(features, threshold=0.6):
    global current_id
    features = normalize_embedding(features)
    best_match_id = None
    highest_similarity = 0

    for person_id, data in person_database.items():
        existing_features = normalize_embedding(data['features'])
        similarity = np.dot(features, existing_features)
        if similarity >= threshold and similarity > highest_similarity:
            highest_similarity = similarity
            best_match_id = person_id

    if best_match_id is not None:
        return best_match_id
    else:
        # Assign a new ID if no match found
        person_database[current_id] = {'features': features}
        current_id += 1
        return current_id - 1

# Assign label to a face based on classifier
def assign_face_label(face_img_gray, confidence_threshold=70):
    face_id, pred = clf.predict(face_img_gray)
    confidence = int(100 * (1 - pred / 300))
    if confidence >= confidence_threshold:
        if face_id == 1:
            return "Soldier", (0, 255, 0)  # Green for Soldier
        elif face_id == 2:
            return "Terrorist", (0, 0, 255)  # Red for Terrorist
    return "Unknown", (255, 0, 0)  # Blue for Unknown

# Function to show a popup warning
def show_popup(person_image, weapon_image=None):
    popup = tk.Tk()
    popup.title("Warning: Possible Threat Detected")
    popup.geometry("400x600")  # Increased size
    tk.Label(popup, text="Threat Detected!", font=("Helvetica", 16), fg="red").pack(pady=10)

    if person_image is not None:
        person_img_pil = Image.fromarray(person_image)
        person_img_pil.thumbnail((300, 300))
        img_tk = ImageTk.PhotoImage(person_img_pil)
        img_label = tk.Label(popup, image=img_tk)
        img_label.image = img_tk
        img_label.pack(pady=10)

    if weapon_image is not None:
        weapon_img_pil = Image.fromarray(weapon_image)
        weapon_img_pil.thumbnail((300, 300))
        weapon_tk = ImageTk.PhotoImage(weapon_img_pil)
        weapon_label = tk.Label(popup, image=weapon_tk)
        weapon_label.image = weapon_tk
        weapon_label.pack(pady=10)

    tk.Button(popup, text="OK", command=popup.destroy).pack(pady=10)
    popup.mainloop()

# Trigger the popup notification in a new thread
def trigger_popup(person_image, weapon_image=None):
    threading.Thread(target=show_popup, args=(person_image, weapon_image)).start()

# Capture video from multiple devices
cap1 = cv2.VideoCapture(0)
cap2 = cv2.VideoCapture(1)

while cap1.isOpened() and cap2.isOpened():
    ret1, frame1 = cap1.read()
    ret2, frame2 = cap2.read()
    if not ret1 or not ret2:
        break

    frames = [frame1, frame2]
    for idx, frame in enumerate(frames):
        weapon_results = weapon_model(frame)
        weapon_boxes = weapon_results[0].boxes.xyxy.cpu().numpy()

        person_results = person_model(frame)
        person_boxes = person_results[0].boxes.xyxy.cpu().numpy()

        for person_box in person_boxes:
            px1, py1, px2, py2 = map(int, person_box[:4])
            person_img = frame[py1:py2, px1:px2]
            person_img_tensor = transform(person_img).unsqueeze(0).to(device)
            with torch.no_grad():
                person_features = reid_model(person_img_tensor).cpu().numpy().flatten()
            person_id = get_person_id(person_features)

            tracked_faces[person_id]["coords"].append((px1, py1, px2, py2))
            avg_coords = np.mean(tracked_faces[person_id]["coords"], axis=0).astype(int)
            px1, py1, px2, py2 = avg_coords

            gray_face = cv2.cvtColor(frame[py1:py2, px1:px2], cv2.COLOR_BGR2GRAY)
            faces = faceCascade.detectMultiScale(gray_face, 1.3, 6)
            for (x, y, w, h) in faces:
                face_label, face_color = assign_face_label(gray_face[y:y+h, x:x+w])
                tracked_faces[person_id]["label"] = face_label

            for weapon_box in weapon_boxes:
                wx1, wy1, wx2, wy2 = map(int, weapon_box)
                if wx1 < px2 and wx2 > px1 and wy1 < py2 and wy2 > py1:  # Overlap
                    person_with_weapon.add(person_id)
                    weapon_img = frame[wy1:wy2, wx1:wx2]

                    if tracked_faces[person_id]["label"] in ["Unknown", "Terrorist"]:
                        current_time = time.time()
                        if current_time - tracked_faces[person_id]["last_alert_time"] >= alert_interval:
                            tracked_faces[person_id]["last_alert_time"] = current_time
                            print(f"Alert: Person ID {person_id} detected with weapon.")
                            trigger_popup(person_img, weapon_img)  # Show popup with person and weapon

                cv2.rectangle(frame, (wx1, wy1), (wx2, wy2), (0, 0, 255), 2)
                cv2.putText(frame, "Weapon", (wx1, wy1 - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0, 0, 255), 2)

            label = tracked_faces[person_id]["label"]
            color = face_color if person_id not in person_with_weapon else (0, 0, 255)
            cv2.rectangle(frame, (px1, py1), (px2, py2), color, 2)
            cv2.putText(frame, label, (px1, py1 - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.5, color, 2)

        cv2.imshow(f'Camera {idx+1}', frame)

    if cv2.waitKey(1) & 0xFF == ord('q'):
        break

cap1.release()
cap2.release()
cv2.destroyAllWindows()

C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\ultralytics\nn\tasks.py:332: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return torch.load(file, map_location='cpu') 

Successfully loaded imagenet pretrained weights from "C:\Users\ganji/.cache\torch\checkpoints\osnet_x1_0_imagenet.pth"


Ultralytics YOLOv8.0.20  Python-3.9.20 torch-2.5.1 CUDA:0 (NVIDIA GeForce RTX 3050 Laptop GPU, 4096MiB)
Model summary (fused): 168 layers, 11126358 parameters, 0 gradients, 28.4 GFLOPs
Ultralytics YOLOv8.0.20  Python-3.9.20 torch-2.5.1 CUDA:0 (NVIDIA GeForce RTX 3050 Laptop GPU, 4096MiB)
Model summary (fused): 168 layers, 11125971 parameters, 0 gradients, 28.4 GFLOPs


Alert: Person ID 3 detected with weapon.
Alert: Person ID 4 detected with weapon.
Alert: Person ID 3 detected with weapon.


Exception in thread Thread-22:
Traceback (most recent call last):
  File "C:\Users\ganji\anaconda3\envs\torch\lib\threading.py", line 980, in _bootstrap_inner
    self.run()
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\sentry_sdk\integrations\threading.py", line 101, in run
    return _run_old_run_func()
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\sentry_sdk\integrations\threading.py", line 96, in _run_old_run_func
    reraise(*_capture_exception())
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\sentry_sdk\utils.py", line 1723, in reraise
    raise value
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\sentry_sdk\integrations\threading.py", line 94, in _run_old_run_func
    return old_run_func(self, *a, **kw)
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\ipykernel\ipkernel.py", line 766, in run_closure
    _threading_Thread_run(self)
  File "C:\Users\ganji\anaconda3\envs\torch\lib\threading.py", line 917, in

...

Alert: Person ID 7 detected with weapon.


Exception in thread Thread-36:
Traceback (most recent call last):
  File "C:\Users\ganji\anaconda3\envs\torch\lib\threading.py", line 980, in _bootstrap_inner
    self.run()
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\sentry_sdk\integrations\threading.py", line 101, in run
    return _run_old_run_func()
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\sentry_sdk\integrations\threading.py", line 96, in _run_old_run_func
    reraise(*_capture_exception())
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\sentry_sdk\utils.py", line 1723, in reraise
    raise value
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\sentry_sdk\integrations\threading.py", line 94, in _run_old_run_func
    return old_run_func(self, *a, **kw)
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\ipykernel\ipkernel.py", line 766, in run_closure
    _threading_Thread_run(self)
  File "C:\Users\ganji\anaconda3\envs\torch\lib\threading.py", line 917, in

Alert: Person ID 4 detected with weapon.
Alert: Person ID 3 detected with weapon.


Exception in thread Thread-41:
Traceback (most recent call last):
  File "C:\Users\ganji\anaconda3\envs\torch\lib\threading.py", line 980, in _bootstrap_inner
    self.run()
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\sentry_sdk\integrations\threading.py", line 101, in run
    return _run_old_run_func()
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\sentry_sdk\integrations\threading.py", line 96, in _run_old_run_func
    reraise(*_capture_exception())
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\sentry_sdk\utils.py", line 1723, in reraise
    raise value
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\sentry_sdk\integrations\threading.py", line 94, in _run_old_run_func
    return old_run_func(self, *a, **kw)
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\ipykernel\ipkernel.py", line 766, in run_closure
    _threading_Thread_run(self)
  File "C:\Users\ganji\anaconda3\envs\torch\lib\threading.py", line 917, in

Alert: Person ID 5 detected with weapon.
Alert: Person ID 2 detected with weapon.
Alert: Person ID 1 detected with weapon.
Alert: Person ID 9 detected with weapon.


In [ ]:
import torch
import torchreid
import cv2
import torchvision.transforms as transforms
from ultralytics import YOLO
import numpy as np
from collections import defaultdict, deque
import time
import tkinter as tk
from PIL import Image, ImageTk
import threading

# Load YOLO models for weapon and person detection
weapon_model = YOLO(r'C:\Users\ganji\Downloads\Weapon 2.v2i.yolov8\runs\detect\train4\weights\best.pt')  # Replace with your weapon model path
person_model = YOLO(r'C:\Users\ganji\Downloads\People Detection.v8i.yolov8\runs\detect\train\weights\best.pt')  # Replace with your person model path

# Initialize OSNet re-ID model
reid_model = torchreid.models.build_model('osnet_x1_0', num_classes=1000, pretrained=True)
reid_model.eval()
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
reid_model = reid_model.to(device)

# Transform for re-ID
transform = transforms.Compose([
    transforms.ToPILImage(),
    transforms.Resize((256, 128)),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
])

# Face detection and recognition
faceCascade = cv2.CascadeClassifier("haarcascade_frontalface_default.xml")
clf = cv2.face.LBPHFaceRecognizer_create()
clf.read("classifier.xml")

# Person tracking database
person_database = {}
person_with_weapon = set()
tracked_faces = defaultdict(lambda: {"coords": deque(maxlen=5), "label": "Unknown", "last_alert_time": 0})
current_id = 1

# Time gap for pop-up notifications
popup_interval = 30  # Seconds

# Function to normalize embeddings
def normalize_embedding(features):
    return features / np.linalg.norm(features)

# Identify person using re-ID embeddings
def get_person_id(features, threshold=0.6):
    global current_id
    features = normalize_embedding(features)
    best_match_id = None
    highest_similarity = 0

    for person_id, data in person_database.items():
        existing_features = normalize_embedding(data['features'])
        similarity = np.dot(features, existing_features)
        if similarity >= threshold and similarity > highest_similarity:
            highest_similarity = similarity
            best_match_id = person_id

    if best_match_id is not None:
        return best_match_id
    else:
        # Assign a new ID if no match found
        person_database[current_id] = {'features': features}
        current_id += 1
        return current_id - 1

# Assign label to a face based on classifier
def assign_face_label(face_img_gray, confidence_threshold=70):
    face_id, pred = clf.predict(face_img_gray)
    confidence = int(100 * (1 - pred / 300))
    if confidence >= confidence_threshold:
        if face_id == 1:
            return "Soldier", (0, 255, 0)  # Green for Soldier
        elif face_id == 2:
            return "Terrorist", (0, 0, 255)  # Red for Terrorist
    return "Unknown", (255, 0, 0)  # Blue for Unknown

# Function to show a popup warning
def show_popup(person_image):
    popup = tk.Tk()
    popup.title("Warning: Threat Detected!")
    popup.geometry("400x500")
    tk.Label(popup, text="Threat Detected!", font=("Helvetica", 16), fg="red").pack(pady=10)

    if person_image is not None:
        person_img_pil = Image.fromarray(person_image)
        person_img_pil.thumbnail((350, 350))
        img_tk = ImageTk.PhotoImage(person_img_pil)
        img_label = tk.Label(popup, image=img_tk)
        img_label.image = img_tk
        img_label.pack(pady=10)

    tk.Button(popup, text="OK", command=popup.destroy).pack(pady=10)
    popup.mainloop()

# Trigger the popup notification in a new thread
def trigger_popup(person_image):
    threading.Thread(target=show_popup, args=(person_image,)).start()

# Capture video feed
cap = cv2.VideoCapture(0)

while cap.isOpened():
    ret, frame = cap.read()
    if not ret:
        break

    # Detect weapons and persons
    weapon_results = weapon_model(frame)
    weapon_boxes = weapon_results[0].boxes.xyxy.cpu().numpy()

    person_results = person_model(frame)
    person_boxes = person_results[0].boxes.xyxy.cpu().numpy()

    for person_box in person_boxes:
        px1, py1, px2, py2 = map(int, person_box[:4])
        person_img = frame[py1:py2, px1:px2]
        person_img_tensor = transform(person_img).unsqueeze(0).to(device)
        with torch.no_grad():
            person_features = reid_model(person_img_tensor).cpu().numpy().flatten()
        person_id = get_person_id(person_features)

        # Update bounding box smoothing
        tracked_faces[person_id]["coords"].append((px1, py1, px2, py2))
        avg_coords = np.mean(tracked_faces[person_id]["coords"], axis=0).astype(int)
        px1, py1, px2, py2 = avg_coords

        gray_face = cv2.cvtColor(frame[py1:py2, px1:px2], cv2.COLOR_BGR2GRAY)
        faces = faceCascade.detectMultiScale(gray_face, 1.3, 6)
        for (x, y, w, h) in faces:
            face_label, face_color = assign_face_label(gray_face[y:y+h, x:x+w])
            tracked_faces[person_id]["label"] = face_label

        # Check if the person is holding a weapon
        for weapon_box in weapon_boxes:
            wx1, wy1, wx2, wy2 = map(int, weapon_box)
            if wx1 < px2 and wx2 > px1 and wy1 < py2 and wy2 > py1:  # Overlap detected
                person_with_weapon.add(person_id)
                tracked_faces[person_id]["last_alert_time"] = 0  # Reset alert time

        # Display bounding boxes and trigger alerts
        if person_id in person_with_weapon:
            label = f'{tracked_faces[person_id]["label"]} (Armed)'
            current_time = time.time()
            if (current_time - tracked_faces[person_id]["last_alert_time"]) >= popup_interval:
                if tracked_faces[person_id]["label"] in ["Unknown", "Terrorist"]:
                    tracked_faces[person_id]["last_alert_time"] = current_time
                    print(f"Alert: {tracked_faces[person_id]['label']} ID {person_id} detected with weapon.")
                    trigger_popup(person_img)  # Show popup

            # Draw red bounding box for threats
            cv2.rectangle(frame, (px1, py1), (px2, py2), (0, 0, 255), 3)
        else:
            label = tracked_faces[person_id]["label"]
            cv2.rectangle(frame, (px1, py1), (px2, py2), face_color, 2)

        cv2.putText(frame, label, (px1, py1 - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.5, face_color, 2)

    cv2.imshow('Camera', frame)

    if cv2.waitKey(1) & 0xFF == ord('q'):
        break

cap.release()
cv2.destroyAllWindows()

C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\torchreid\reid\metrics\rank.py:11: UserWarning: Cython evaluation (very fast so highly recommended) is unavailable, now use python evaluation.
  warnings.warn(
C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\ultralytics\nn\tasks.py:332: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weight

Successfully loaded imagenet pretrained weights from "C:\Users\ganji/.cache\torch\checkpoints\osnet_x1_0_imagenet.pth"


Ultralytics YOLOv8.0.20  Python-3.9.20 torch-2.5.1 CUDA:0 (NVIDIA GeForce RTX 3050 Laptop GPU, 4096MiB)
Model summary (fused): 168 layers, 11126358 parameters, 0 gradients, 28.4 GFLOPs
Ultralytics YOLOv8.0.20  Python-3.9.20 torch-2.5.1 CUDA:0 (NVIDIA GeForce RTX 3050 Laptop GPU, 4096MiB)
Model summary (fused): 168 layers, 11125971 parameters, 0 gradients, 28.4 GFLOPs


Alert: Terrorist ID 1 detected with weapon.
Alert: Terrorist ID 1 detected with weapon.


Exception in thread Thread-7:
Traceback (most recent call last):
  File "C:\Users\ganji\anaconda3\envs\torch\lib\threading.py", line 980, in _bootstrap_inner
    self.run()
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\sentry_sdk\integrations\threading.py", line 101, in run
    return _run_old_run_func()
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\sentry_sdk\integrations\threading.py", line 96, in _run_old_run_func
    reraise(*_capture_exception())
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\sentry_sdk\utils.py", line 1723, in reraise
    raise value
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\sentry_sdk\integrations\threading.py", line 94, in _run_old_run_func
    return old_run_func(self, *a, **kw)
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\ipykernel\ipkernel.py", line 766, in run_closure
    _threading_Thread_run(self)
  File "C:\Users\ganji\anaconda3\envs\torch\lib\threading.py", line 917, in 

...

Alert: Unknown ID 2 detected with weapon.
Alert: Unknown ID 2 detected with weapon.
Alert: Unknown ID 3 detected with weapon.
Alert: Unknown ID 4 detected with weapon.


Exception in thread Thread-30:
Traceback (most recent call last):
  File "C:\Users\ganji\anaconda3\envs\torch\lib\threading.py", line 980, in _bootstrap_inner
    self.run()
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\sentry_sdk\integrations\threading.py", line 101, in run
    return _run_old_run_func()
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\sentry_sdk\integrations\threading.py", line 96, in _run_old_run_func
    reraise(*_capture_exception())
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\sentry_sdk\utils.py", line 1723, in reraise
    raise value
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\sentry_sdk\integrations\threading.py", line 94, in _run_old_run_func
    return old_run_func(self, *a, **kw)
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\ipykernel\ipkernel.py", line 766, in run_closure
    _threading_Thread_run(self)
  File "C:\Users\ganji\anaconda3\envs\torch\lib\threading.py", line 917, in

Alert: Terrorist ID 1 detected with weapon.
Alert: Unknown ID 4 detected with weapon.


Exception in thread Thread-35:
Traceback (most recent call last):
  File "C:\Users\ganji\anaconda3\envs\torch\lib\threading.py", line 980, in _bootstrap_inner
    self.run()
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\sentry_sdk\integrations\threading.py", line 101, in run
    return _run_old_run_func()
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\sentry_sdk\integrations\threading.py", line 96, in _run_old_run_func
    reraise(*_capture_exception())
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\sentry_sdk\utils.py", line 1723, in reraise
    raise value
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\sentry_sdk\integrations\threading.py", line 94, in _run_old_run_func
    return old_run_func(self, *a, **kw)
  File "C:\Users\ganji\anaconda3\envs\torch\lib\site-packages\ipykernel\ipkernel.py", line 766, in run_closure
    _threading_Thread_run(self)
  File "C:\Users\ganji\anaconda3\envs\torch\lib\threading.py", line 917, in

Alert: Unknown ID 4 detected with weapon.
